# PSTAT 100 Final Project: Socioeconomic Factors Behind Regional and Temporal Differences in Happiness
### By Ethan Choi and Alex Zhao

## Data Description

In this project, we chose to work with was the World Happiness Report 2023. This report contains the happiness level (also called life ladder score) of 165 countries around the world from years between 2005 and 2022, as well as a variety of socioeconomic factors. Life ladder (happiness level) is an important measurement in our society as it quantifies and reflects the physical and mental well-being of individuals and enables effective comparisons across time and places. In this dataset, the observational units are countries, and one observation is made for each country at each year from 2005 to 2022 (inclusive). The dataset is comprised a total of 2199 observations and 11 distinct variables, including country name, year, Life Ladder, log(GDP per capita), social support, healthy life expectancy at birth, freedom to make life choices, generosity, perceptions of corruption, positive affect, and negative affect. The main variable of interest is the Life Ladder, which has a mean of 5.479, a standard deviation of 1.13, with its minimum and maximum being 1.281 and 8.019, respectively. We are also interested in other variables that potentially have an association or relationship with Life Ladder. For example, the logarithm of GDP per capita has a mean of 9.390, a standard deviation of 1.153, with minimum and maximum values being 5.527 and 11.664. In addition, it is important to note that this data was collected from 165 different countries, but not all 165 of those countries participated in the report every year from 2005-2022. For example, we do not have an observation from Afghanistan in 2005. Therefore, there are missing observations in this dataset, but it does not pose a serious problem to our analysis as none of the variables are missing over 5.5% of the time. A table of summary statistics, which provides us with a good base line for comparing countries' happiness levels and socioeconomic factors, is displayed below for further reference.

The World Happiness Report obtained samples that used to calculate socioeconomic factors on a national level from a variety of sources, including the World Development Indicators (WDI), World Health Organization (WHO), and the Gallup World Poll (GWP). It is worth noting that the GWP utilized random-digit-dial (RDD) to carry out telephone surveys and random selection to conduct face-to-face interviews in their random sampling process. 

The table below provides the detailed description of the socioeconomic variables, each of which corresponds to a column in the dataframe. 

Variable name | Description 
--------------|--------------
`Life Ladder` | National average of answers to question: "How would you rate your current life on a scale from 0-10?" With 0 being the worst and 10 being the best. 
`Log GDP per capita` | Logarithm of GDP per capita in terms of Purchasing Power Parity adjusted to constant 2017 international dollars. 
`Social Support` | National average of answers to question: "If you were in trouble, do you have relatives or friends you can count on to help you whenever you need them, or not?” With 0=No and 1=Yes.
`Healthy life expectancy at birth` | Healthy life expectancy based on time series analysis of World Health Organization data (in years).
`Freedom to make life choices` |National average of answers to question: "Are you satisfied or dissatisfied with your freedom to choose what you do with your life??” With 0=Dissatisfied and 1=Satisfied.
`Generosity` |Residual of regressing the national average of answers to the question “Have you donated money to a charity in the past month?” on log GDP per capita.
`Perceptions of corruption` |National average of answers to the two questions: “Is corruption widespread throughout the government or not?” and “Is corruption widespread within businesses or not?” With 0=No and 1=Yes.
`Positive affect` | National average of previous-day affect measures for laughter, enjoyment, and interest. Questions are asked in the form of "Did you experience the following feelings during a lot of the day yesterday?"
`Negative affect` | National average of previous-day affect measures for worry, sadness, and anger. Questions are asked in the form of "Did you experience the following feelings during a lot of the day yesterday?"

### Data Cleaning and Wrangling

In [1]:
# Load packages
import numpy as np
import pandas as pd
import altair as alt
from scipy import linalg
from statsmodels.multivariate.pca import PCA
from sklearn.decomposition import PCA
import statsmodels.api as sm
# disable row limit for plotting
alt.data_transformers.disable_max_rows()
# uncomment to ensure graphics display with pdf export
# alt.renderers.enable('mimetype')

DataTransformerRegistry.enable('default')

In [2]:
## (i) import tidy world happiness data
happiness = pd.read_csv('data/whr-2023.csv')
happiness.head()

Country name  year  Life Ladder  Log GDP per capita  Social support  \
0  Afghanistan  2008        3.724               7.350           0.451   
1  Afghanistan  2009        4.402               7.509           0.552   
2  Afghanistan  2010        4.758               7.614           0.539   
3  Afghanistan  2011        3.832               7.581           0.521   
4  Afghanistan  2012        3.783               7.661           0.521   

   Healthy life expectancy at birth  Freedom to make life choices  Generosity  \
0                              50.5                         0.718       0.168   
1                              50.8                         0.679       0.191   
2                              51.1                         0.600       0.121   
3                              51.4                         0.496       0.164   
4                              51.7                         0.531       0.238   

   Perceptions of corruption  Positive affect  Negative affect  
0                      0.882            0.414            0.258  
1                      0.850            0.481            0.237  
2                      0.707            0.517            0.275  
3                      0.731            0.480            0.267  
4                      0.776            0.614            0.268

In [3]:
## (ii) how many observations are in the data set
happiness.shape

(2199, 11)

In [4]:
## (iii) how many countries are in the data set
happiness['Country name'].nunique()

165

In [5]:
## (iv) which years do the observations come from
np.sort(happiness['year'].unique())

array([2005, 2006, 2007, 2008, 2009, 2010, 2011, 2012, 2013, 2014, 2015,
       2016, 2017, 2018, 2019, 2020, 2021, 2022])

In [6]:
## (v) how often are variable values missing
happiness.isna().mean()

Country name                        0.000000
year                                0.000000
Life Ladder                         0.000000
Log GDP per capita                  0.009095
Social support                      0.005912
Healthy life expectancy at birth    0.024557
Freedom to make life choices        0.015007
Generosity                          0.033197
Perceptions of corruption           0.052751
Positive affect                     0.010914
Negative affect                     0.007276
dtype: float64

In [7]:
## (vi) summary statistics
happiness_summary = happiness.drop(columns = ['Country name', 'year']).aggregate(['mean','std','min','max']).transpose()

# print the dataframe
happiness_summary

mean       std    min     max
Life Ladder                        5.479227  1.125527  1.281   8.019
Log GDP per capita                 9.389760  1.153402  5.527  11.664
Social support                     0.810681  0.120953  0.228   0.987
Healthy life expectancy at birth  63.294582  6.901104  6.720  74.475
Freedom to make life choices       0.747847  0.140137  0.258   0.985
Generosity                         0.000091  0.161079 -0.338   0.703
Perceptions of corruption          0.745208  0.185835  0.035   0.983
Positive affect                    0.652148  0.105913  0.179   0.884
Negative affect                    0.271493  0.086872  0.083   0.705

## Questions of Interest

We are particularly interested in the regional and temporal differences in Life Ladder (also known as the happiness level) and their corresponding influencing factors. To find out, we propose two major questions for our analysis. First, are there statistically significant differences in life ladder between different regions of the world (in particular, between Africa and the Americas)? If so, which variables account for these differences the most? Second, has happiness around the world improved over time, and are there statistically significant differences in life ladder before 2014 (inclusive) and after 2014 (not inclusive)? If so, which variables explain the variations and account for these differences the most? 

These questions interested us because we are hopeful that peoples' happiness has improved over time and wanted to provide a definitive answer. We also believe it is important to identify variables that can explain trends in different countries' happiness levels. In that way, we can discover why certain countries may be happier than others, and what actions should government, institutions, or organizations around the world possibly take to effectively address those disparities and promote happiness in their countries.

A satisfactory answer to our question would be showing a statistically significant trend in life ladder over time and a statisticallly significant difference in life ladder across different regions, in addition to a list of variables that explain the most variation (derived from principal component analysis) and account for these regional and temporal variations.

## Data Analysis

### Exploratory Data Analysis

In order to tackle these problems we will first derive some overall trends in the data in our exploratory analysis such as, has there been an overall improvement in happiness around the world, which country has seen the greatest improvement in happiness, and which country has been the happiest over time. We will then attempt to examine these trends further and provide plausible explanations using techniques including principal component analysis and multiple linear regression.

#### Has happiness around the world improved over time?
We will address this question by constructing dataframes and presenting figures indicating the trend over time.

In [8]:
# Average life ladder score across all countries each year from 2005-2022
happiness_byyear = happiness.iloc[:,[1,2]].groupby('year').mean().reset_index()
happiness_byyear

year  Life Ladder
0   2005     6.446259
1   2006     5.196899
2   2007     5.418275
3   2008     5.418509
4   2009     5.457667
5   2010     5.496806
6   2011     5.424082
7   2012     5.443617
8   2013     5.393294
9   2014     5.386264
10  2015     5.400944
11  2016     5.396447
12  2017     5.460408
13  2018     5.498674
14  2019     5.570965
15  2020     5.727517
16  2021     5.636246
17  2022     5.585140

In [9]:
# Plot of above dataframe
fig1 = alt.Chart(happiness_byyear).mark_line(point=True).encode(
    x = 'year:N',
    y = alt.Y('Life Ladder', scale=alt.Scale(domain=[5,7]))).properties(
    title = 'Figure 1: Average Happiness Around the World Over Time (2005-2022)')
# Display
fig1

alt.Chart(...)

The ladder score in 2005 (6.45) appears to be an outlier, therefore we checked the sample size of countries used to obtain this score.

In [10]:
# Number of countries surveryed in 2005
len(happiness[happiness['year']==2005])

27

Only 27 countries out of the 165 total countries that appeared in this report had happiness data from 2005. This led us to look at the number of countries surveyed each year.

In [11]:
# Checking amount of countries surveyed each year
results = []

for year in range(2005, 2023):
    result_tuple = (year, len(happiness[happiness['year'] == year]))
    results.append(result_tuple)

df = pd.DataFrame(results, columns=['Year', 'Number of Countries Surveyed'] )

# Display the resulting DataFrame.
df['Proportion of Total Countries'] = df['Number of Countries Surveyed']/165
df

Year  Number of Countries Surveyed  Proportion of Total Countries
0   2005                            27                       0.163636
1   2006                            89                       0.539394
2   2007                           102                       0.618182
3   2008                           110                       0.666667
4   2009                           114                       0.690909
5   2010                           124                       0.751515
6   2011                           146                       0.884848
7   2012                           141                       0.854545
8   2013                           136                       0.824242
9   2014                           144                       0.872727
10  2015                           142                       0.860606
11  2016                           141                       0.854545
12  2017                           147                       0.890909
13  2018                           141                       0.854545
14  2019                           143                       0.866667
15  2020                           116                       0.703030
16  2021                           122                       0.739394
17  2022                           114                       0.690909

We are able to notice that 2005 is the only year in which less than 50% of the 165 total countries in the report, were surveyed. Since only about 16% of these countries were surveyed in 2005, we decided to remove observations from 2005 when deciding whether or not happiness improved around the world over time. This is because we thought that data from only 27 countries was not sufficient enough to represent the entire world. So, we replotted the happiness data grouped by year, removing observations from 2005, and got the following results:

In [12]:
# Average life ladder score across all countries each year form 2006-2022
happiness_byyear_no2005 = happiness_byyear[happiness_byyear['year']!=2005]
happiness_byyear_no2005

year  Life Ladder
1   2006     5.196899
2   2007     5.418275
3   2008     5.418509
4   2009     5.457667
5   2010     5.496806
6   2011     5.424082
7   2012     5.443617
8   2013     5.393294
9   2014     5.386264
10  2015     5.400944
11  2016     5.396447
12  2017     5.460408
13  2018     5.498674
14  2019     5.570965
15  2020     5.727517
16  2021     5.636246
17  2022     5.585140

In [13]:
# Life Ladder Over Time with Outliers removed
fig2 = alt.Chart(happiness_byyear_no2005).mark_line(point=True).encode(
    x = 'year:N',
    y = alt.Y('Life Ladder', scale=alt.Scale(domain=[5,6]))).properties(
    title = 'Figure 2: Average Happiness Around the World Over Time (2006-2022)')
# Display
fig2

alt.Chart(...)

From this graph, we can see that since 2006, there has been a slight increase in the overall happiness in the world with the life ladder score increasing from approximately 5.2 in 2006 to approximately 5.59 in 2022.

#### Which country's happiness has improved the most over time?
We will address this question by constructing dataframes and presenting figures indicating the trend over time.

In [14]:
afghanistan = happiness[happiness['Country name'] == 'Afghanistan']
afghanistan.loc[len(afghanistan)-1,'Life Ladder']-afghanistan.loc[0,'Life Ladder']

-2.4430000000000005

In [15]:
countries = happiness['Country name'].unique()
results = []

for country in countries:
    country_data = happiness[happiness['Country name'] == country].reset_index()
    difference = country_data.loc[len(country_data) - 1, 'Life Ladder'] - country_data.loc[0, 'Life Ladder']
    result_tuple = (country, difference)
    results.append(result_tuple)

df = pd.DataFrame(results, columns=['Country', 'Increase in Happiness'])

df[df['Increase in Happiness']==df['Increase in Happiness'].max()]

Country  Increase in Happiness
32  Congo (Brazzaville)                  1.985

In [16]:
# Figure 3: Happiness in Congo (Brazzaville) Over Time
fig3 = alt.Chart(happiness[happiness['Country name'] == 'Congo (Brazzaville)']).mark_line(point=True).encode(
    x = 'year:N',
    y = alt.Y('Life Ladder', scale=alt.Scale(domain=[3.5,6]))).properties(
    title = 'Figure 3: Happiness in Congo (Brazzaville) Over Time')
# Display
fig3

alt.Chart(...)

In order to quantify the "greatest improvement" in happiness over time, we took the most oldest life ladder score from each country and subtracted it from that country's most recent life ladder score. Thus, we found that Congo (Brazzaville), also known as the Repubilic of Congo (not to be confused with the Democratic Republic of Congo), has seen the greatest improvement in happiness with their Life Ladder score increasing by nearly 2 points between 2008 and 2022.

#### Which country has consistently been the happiest?

In [17]:
# Which country has consistently been the happiest
happiness_bycountry = happiness.iloc[:,[0,2]].groupby('Country name').mean().reset_index()
happiness_bycountry
happiness_bycountry[happiness_bycountry['Life Ladder']==happiness_bycountry['Life Ladder'].max()]

Country name  Life Ladder
39      Denmark     7.673529

In [18]:
happiness[happiness['Country name']=='Denmark']

Country name  year  Life Ladder  Log GDP per capita  Social support  \
505      Denmark  2005        8.019              10.849           0.972   
506      Denmark  2007        7.834              10.889           0.954   
507      Denmark  2008        7.971              10.878           0.954   
508      Denmark  2009        7.683              10.822           0.939   
509      Denmark  2010        7.771              10.836           0.975   
510      Denmark  2011        7.788              10.845           0.962   
511      Denmark  2012        7.520              10.844           0.951   
512      Denmark  2013        7.589              10.849           0.965   
513      Denmark  2014        7.508              10.860           0.956   
514      Denmark  2015        7.514              10.876           0.960   
515      Denmark  2016        7.558              10.900           0.954   
516      Denmark  2017        7.594              10.922           0.952   
517      Denmark  2018        7.649              10.936           0.958   
518      Denmark  2019        7.693              10.948           0.958   
519      Denmark  2020        7.515              10.924           0.947   
520      Denmark  2021        7.699              10.968           0.945   
521      Denmark  2022        7.545              10.994           0.970   

     Healthy life expectancy at birth  Freedom to make life choices  \
505                            68.300                         0.971   
506                            68.740                         0.932   
507                            68.960                         0.970   
508                            69.180                         0.949   
509                            69.400                         0.944   
510                            69.620                         0.935   
511                            69.840                         0.933   
512                            70.060                         0.920   
513                            70.280                         0.942   
514                            70.500                         0.941   
515                            70.625                         0.948   
516                            70.750                         0.955   
517                            70.875                         0.935   
518                            71.000                         0.963   
519                            71.125                         0.938   
520                            71.250                         0.933   
521                            71.375                         0.930   

     Generosity  Perceptions of corruption  Positive affect  Negative affect  
505         NaN                      0.237            0.777            0.154  
506       0.236                      0.206            0.778            0.194  
507       0.268                      0.248            0.759            0.163  
508       0.259                      0.206            0.782            0.234  
509       0.238                      0.175            0.796            0.155  
510       0.293                      0.220            0.778            0.175  
511       0.135                      0.187            0.783            0.209  
512       0.211                      0.170            0.826            0.195  
513       0.114                      0.237            0.780            0.233  
514       0.218                      0.191            0.801            0.218  
515       0.134                      0.210            0.786            0.208  
516       0.151                      0.181            0.779            0.206  
517       0.013                      0.151            0.773            0.206  
518       0.016                      0.174            0.797            0.181  
519       0.047                      0.214            0.753            0.227  
520       0.131                      0.173            0.792            0.206  
521       0.224                

In [19]:
# Figure 4: Happiness in Denmark Over Time
fig4 = alt.Chart(happiness[happiness['Country name'] == 'Denmark']).mark_line(point=True).encode(
    x = 'year:N',
    y = alt.Y('Life Ladder', scale=alt.Scale(domain=[5,9]))).properties(
    title = 'Figure 4: Happiness in Denmark Over Time')
# Display
fig4

alt.Chart(...)

#### What about these trends?

In order to establish whcih country has _consistently_ been the happiest, we simply looked at the average life ladder score of each country between 2005 and 2022. We found that Denmark has consistently been the most happy country between 2005 and 2022 with an average life ladder score of about 7.67 during this time period.

Now that we have established that: there has been a slight increase in the overall hapiness in the world, Congo (Brazzaville) has seen the largest increase in happiness, and Denmark has consistenly been the most happy country. 

However, we don't have a clear conclusion yet about whether this increasing trend is actually statistically significant. We also believe it is worthy and interesting to look at life ladder scores by regions (Asia, Americas, Africa, Europe, and Oceania) and periods (before 2014 and after 2014). In the end, we still have to give an explanation on what variables is related for these trends as well as differences across regions and periods. In order to do so, we will perform further exploratory analysis, then principal component analysis and multiple linear regressions.

In [20]:
# Create a copy for exploratory analysis
happ = happiness.copy()
# Defining 5 regions that we want to focus on
asia = ['Bangladesh', 'Bahrain', 'Hong Kong S.A.R. of China', 'United Arab Emirates', 'Thailand', 'Iraq', 
        'Laos', 'Cambodia', 'Yemen', 'Mongolia', 'Taiwan Province of China', 'Kazakhstan', 'Turkiye', 'Tajikistan', 
        'Malaysia', 'Saudi Arabia', 'Myanmar', 'India', 'Oman', 'Kuwait', 'Indonesia', 'Bhutan', 'Syria', 
        'Pakistan', 'Qatar', 'Israel', 'Philippines', 'Jordan', 'China', 'Nepal', 'Uzbekistan', 'Lebanon', 
        'Vietnam', 'Iran', 'Singapore', 'Sri Lanka', 'South Korea', 'Armenia', 'Afghanistan', 'Azerbaijan', 
        'Japan', 'Kyrgyzstan', 'Maldives', 'State of Palestine', 'Turkmenistan']

europe = ['Bulgaria', 'Spain', 'Greece', 'Italy', 'Germany', 'Czechia', 'Hungary', 'Portugal', 'Belgium', 'Latvia', 
          'Austria', 'Luxembourg', 'Bosnia and Herzegovina', 'Ireland', 'Slovakia', 'Serbia', 'Belarus', 'Estonia', 
          'Norway', 'Slovenia', 'United Kingdom', 'Iceland', 'Poland', 'Lithuania', 'Croatia', 'Finland', 'Moldova', 
          'Ukraine', 'Montenegro', 'Sweden', 'Denmark', 'France', 'Russia', 'Romania', 'Netherlands', 'Switzerland',
         'Cyprus', 'Georgia', 'Albania', 'Kosovo', 'Malta', 'North Macedonia']

africa = ['Ghana', 'Namibia', 'Rwanda', 'Senegal', 'Botswana', 'Malawi', 'South Sudan', 'Togo', 'Madagascar', 
          'Cameroon', 'Sudan', 'Angola', 'Mauritius', 'Mauritania', 'Chad', 'Lesotho', 'Uganda', 'Benin', 'Morocco', 
          'Gambia', 'Congo (Brazzaville)', 'Ethiopia', 'Cape Verde', 'Niger', 'Mali', 'Sierra Leone', 'Ivory Coast', 
          'South Africa', 'Guinea', 'Kenya', 'Zambia', 'Zimbabwe', 'Mozambique', 'Burkina Faso', 'Central African Republic', 
          'Gabon', 'Algeria', 'Tanzania', 'Egypt', 'Nigeria', 'Djibouti', 'Burundi', 'Comoros', 'Congo (Kinshasa)',
         'Eswatini', 'Liberia', 'Libya', 'Somalia', 'Somaliland region', 'Tunisia']

americas = ['United States', 'Canada', 'Belize', 'Peru', 'Costa Rica', 'El Salvador', 'Haiti', 'Paraguay', 'Panama', 
            'Venezuela', 'Guyana', 'Argentina', 'Jamaica', 'Ecuador', 'Suriname', 'Brazil', 'Colombia', 'Chile', 
            'Dominican Republic', 'Bolivia', 'Mexico', 'Honduras', 'Uruguay', 'Nicaragua', 'Trinidad and Tobago', 
            'Cuba', 'Guatemala']

oceania = ['Australia', 'New Zealand']

# Defining 2 periods that we want to focus on
period1 = [2006, 2007, 2008, 2009]
period2 = [2020, 2021, 2022]

# Defining a function that assigns region name to each country
def region_to(country):
    if country in asia:
        return 'Asia'
    elif country in europe:
        return 'Europe'
    elif country in americas:
        return 'Americas'
    elif country in africa:
        return 'Africa'
    elif country in oceania:
        return 'Oceania'
    else:
        return 'Other'
    
# Defining a function that assigns periods depending on year
def period_to(year):
    if year in period1:
        return 'Pre-2010 (2006-2009)'
    elif year in period2:
        return 'Post-2020 (2020-2022)'
    else:
        return 'Others'

# Applying the function `region_to` and `period_to` to each row
happ['Region'] = happ['Country name'].apply(region_to)
happ['Period'] = happ['year'].apply(period_to)
# Switch order of columns to connect country name and region, year and period
happ.insert(1, 'Region', happ.pop(happ.columns[-2]))
happ.insert(3, 'Period', happ.pop(happ.columns[-1]))
# Preview
happ.head()

Country name Region  year                Period  Life Ladder  \
0  Afghanistan   Asia  2008  Pre-2010 (2006-2009)        3.724   
1  Afghanistan   Asia  2009  Pre-2010 (2006-2009)        4.402   
2  Afghanistan   Asia  2010                Others        4.758   
3  Afghanistan   Asia  2011                Others        3.832   
4  Afghanistan   Asia  2012                Others        3.783   

   Log GDP per capita  Social support  Healthy life expectancy at birth  \
0               7.350           0.451                              50.5   
1               7.509           0.552                              50.8   
2               7.614           0.539                              51.1   
3               7.581           0.521                              51.4   
4               7.661           0.521                              51.7   

   Freedom to make life choices  Generosity  Perceptions of corruption  \
0                         0.718       0.168                      0.882   
1                         0.679       0.191                      0.850   
2                         0.600       0.121                      0.707   
3                         0.496       0.164                      0.731   
4                         0.531       0.238                      0.776   

   Positive affect  Negative affect  
0            0.414            0.258  
1            0.481            0.237  
2            0.517            0.275  
3            0.480            0.267  
4            0.614            0.268

#### Regional Differences

We will first examine life ladder score across five different regions of the world, including Africa, Americas, Asia, Europe, and Oceania. To illustrate the regional differences in the life ladder socres, we created a box plot to display the scores by region. According to figure 5, we noticed that countries in Oceania demonstrated the highest level of life ladder score distribution, with the median being 7.257, minimum being 6.975 and maximum being 7.604. Countries in Europe and the Americas (including both North America and Latin America) also have fairly high levels of life ladder scores. Specifically, European countries have median of 6.119 and countries in the Americas have a median of 6.136. Asia is behind Europe and the Americas, and Africa has the lowest life ladder score compared to the rest of the world, with a median of 4.396, minimum of 2.56 and maximum of 6.355.

In [21]:
# Figure 5: Life Ladder by Region
fig5 = alt.Chart(happ).mark_boxplot(size = 60).encode(
    x='Region:N',
    y='Life Ladder:Q',
    color='Region:N'
).properties(
    width = 400,
    height = 400,
    title = 'Figure 5: Life Ladder by Region'
)

# Display
fig5

alt.Chart(...)

#### Temporal Differences
We then study the distribution of life ladder scores in two different periods: one is called Pre-2010 (from 2006 to 2009), whereas the other named Post-2020 (2020-2022). We hope to find out whether there is a significant difference in happiness between period that is farthest from us in this dataset and the period that is closer to us in terms of time. According to figure 6, pre-2010 period has its highest estimated density at around 5.2, whereas post-2020 period has its highest density at around 5.8. Therefore, there seems to be a slight improvement in life ladder scores over time, but we are unsure of the extent of statistical significance. This is a question that we will be focusing on when running multiple linear regressions.

In [22]:
# Figure 6: KDE of Life Ladder in Pre-2010 vs Post-2020
fig6 = alt.Chart(happ).transform_filter(
    alt.FieldOneOfPredicate(field = 'Period',
                            oneOf = ['Pre-2010 (2006-2009)', 'Post-2020 (2020-2022)'])
).transform_density(
    density = 'Life Ladder',
    groupby = ['Period'],
    as_ = ['Life Ladder', 'Estimated Density'],
    bandwidth = 1, 
    extent = [0, 10],
    steps = 1000 
).mark_line().encode(
    x = 'Life Ladder:Q',
    y = 'Estimated Density:Q',
    color = 'Period:N'
).properties(
    title = 'Figure 6: KDE of Life Ladder in Pre-2010 vs Post-2020'
)
# Display
fig6 + fig6.mark_area(opacity = 0.2)

alt.LayerChart(...)

#### Variables of Interest

We then observe the relationships between the life ladder score and each of the socioeconomic varibles given in the dataset by creating faceted scatterplots since we are particularly interested in the potential associations among them. We noticed that there is likely a positive correlation between life ladder and freedom to make life choices, healthy life expectancy at birth, log(GDP per capita), positive affect, and social support. On the other hand, there is likely a negative correlation between life ladder and negative affect as well as life ladder and perceptions of corruption. By looking at the scatterplot, we believe the correlation between life ladder and generosity is very weak. We will further examine the strength of each variable on life ladder in MLR models.

In [23]:
# Figure 7: Life Ladder against Socioeconomic Variables
happ_m = happ.melt(
    id_vars = ['Country name', 'Region', 'year', 'Life Ladder'],
    var_name = 'Variable',
    value_name = 'Value'
)

fig7 = alt.Chart(happ_m).mark_circle(opacity = 0.3).encode(
    x=alt.X('Value:Q', title=' '),
    y=alt.Y('Life Ladder:Q', title='Life Ladder'),
    color='Variable:N'
).facet(
    facet = 'Variable:N',
    columns = 2
).resolve_scale(
    x='independent'
).properties(
    title = 'Figure 7: Correlations Between Socioeconomic Variables and Life Ladder'
)

# Display
fig7

alt.FacetChart(...)

#### What did we learn from exploratory data analysis?

From the exploratory analysis above, we are able to observe differences in life ladder scores across different regions and periods. It is clear that people in different countries and regions of the world as well as people living in different periods had entirely different perceptions of happiness due to various factors (as shown in figure 7), thereby resulting in gaps in life ladder scores.

#### What's next?

Besides countries in Ocenaia, which we will not be focusing on because only two countries (Austrialia and New Zealand) are sampled, we see that American countries and African countries have the most significant difference in medians of life ladder score. Therefore, an important question originates from our exploratory analysis above: is the difference in happiness between African countries and American countries statistically significant? If so, what are the most significant factors that contribute to this statistically significant difference? What about differences in life ladder scores between pre-2010 and post-2020?

## Data Analysis
### Regression Analysis

To address this question, we will use a combination of principal component analysis (PCA) and regression models. First, we want to address whether the hypothesized regional and temporal differences are statistically significant by constructing two simple regression models:

$$\text{LifeLadder} = \beta_0 + \beta_1 \text{Region} + \epsilon$$

$$\text{LifeLadder} = \beta_0 + \beta_1 \text{Period} + \epsilon$$
where 
1. $Region$ is a dummy variable to indicate whether the country is in the Americas or otherwise in Africa such that $Region = \begin{cases} 
      1 & \text{if in the Americas} \\
      0 & \text{otherwise (in Africa)}
   \end{cases}$

2. $Period$ is also a dummy variable to indicate whether the observation is from pre-2010 or post-2020 such that $Period = \begin{cases} 
      1 & \text{if in post-2020 (2020-2022)} \\
      0 & \text{otherwise in pre-2010 (2007-2009)}
   \end{cases}$
To get started, further data manipulation needs to be carried out.

In [24]:
# Is the difference in Life Ladder between Americas and Africa significant?
# 1. Regression - 
happ_region = happ.copy()[happ.Region.isin(['Americas', 'Africa'])].reset_index(
).drop(
    columns = ['index']
).dropna(
    axis = 0,
    how = 'any'
)

# Dummy Variable
happ_region['Region'] = happ_region['Region'].replace({'Americas':1,'Africa':0})
happ_region

# retrieve response
y = happ_region['Life Ladder']

# construct explanatory variable matrix
x = sm.tools.add_constant(happ_region.loc[:, ['Region']])

# fit model
mlr_region = sm.OLS(endog = y, exog = x)
rslt_region = mlr_region.fit()
coef_tbl_region = pd.DataFrame({
    'estimate': rslt_region.params.values,
    'standard error': np.sqrt(rslt_region.cov_params().values.diagonal()) 
    },
    index = x.columns 
)

coef_tbl_region.loc['error variance', 'estimate'] = rslt_region.scale

# R^2
print('The R^2 is', rslt_region.rsquared)
coef_tbl_region

The R^2 is 0.5968458490836221


estimate  standard error
const           4.367093        0.030994
Region          1.737785        0.048534
error variance  0.493776             NaN

In [25]:
# Is the difference in Life Ladder between pre-2010 and post-2020
# SLR
happ_region = happ.copy()[happ.Period.isin(['Pre-2010 (2006-2009)', 'Post-2020 (2020-2022)'])].reset_index(
).drop(
    columns = ['index']
).dropna(
    axis = 0,
    how = 'any'
)

# Dummy Variable
happ_region['Period'] = happ_region['Period'].replace({'Pre-2010 (2006-2009)':0,
                                                       'Post-2020 (2020-2022)':1})
happ_region

# retrieve response
y = happ_region['Life Ladder']

# construct explanatory variable matrix
x = sm.tools.add_constant(happ_region.loc[:, ['Period']])

# fit model
mlr_period = sm.OLS(endog = y, exog = x)
rslt_period = mlr_period.fit()
coef_tbl_period = pd.DataFrame({
    'estimate': rslt_period.params.values,
    'standard error': np.sqrt(rslt_period.cov_params().values.diagonal()) 
    },
    index = x.columns 
)
# Estimates of coefficients + standard errors
coef_tbl_period.loc['error variance', 'estimate'] = rslt_period.scale

# R^2
print('The R^2 is', rslt_region.rsquared)
coef_tbl_period

The R^2 is 0.5968458490836221


estimate  standard error
const           5.383718        0.057715
Period          0.266557        0.084721
error variance  1.242474             NaN

To have a clear understanding of the strenth of those socioeconomic variables on the dependent variable life ladder, we will also run a multiple linear regression and find the estimated coefficients.

$$\text{LifeLadder} = \beta_0 + \beta_1 \text{log(GDP per capita)} + \beta_2 \text{Freedom to make life choices} + \beta_3\text{Perceptions of corruption} + \beta_5 \text{Social support} + \beta_6\text{Positive affect} + \epsilon$$



In [26]:
# 3. Regression - What relationship can we find between each of the socioeconomic variables
# and the life ladder index
# Notice that Healthy life expectancy at birth and Generosity are removed because
# the former has high correlation with log(GDP per capita) and the latter does not
# demonstrate a clear linear relationship
happ_reg = happ.copy().reset_index().drop(
    columns = ['index']
).dropna()

# retrieve response
y = happ_region['Life Ladder']

# construct explanatory variable matrix
x = sm.tools.add_constant(
    happ_region.loc[:, ['Log GDP per capita',
                        'Freedom to make life choices',
                        'Perceptions of corruption',
                        'Social support',
                        'Positive affect']]
)
                                             
# fit model
mlr_general = sm.OLS(endog = y, exog = x)
rslt_general = mlr_general.fit()
coef_tbl_general = pd.DataFrame({
    'estimate': rslt_general.params.values,
    'standard error': np.sqrt(rslt_general.cov_params().values.diagonal()) 
    },
    index = x.columns 
)
# Estimates of coefficients + standard errors
coef_tbl_general.loc['error variance', 'estimate'] = rslt_general.scale

# R^2
print('The R^2 is', rslt_general.rsquared)
coef_tbl_general

The R^2 is 0.7946658337651922


estimate  standard error
const                        -2.010688        0.268998
Log GDP per capita            0.498505        0.026359
Freedom to make life choices  0.590551        0.181003
Perceptions of corruption    -0.873125        0.127322
Social support                1.833399        0.240035
Positive affect               2.423744        0.232894
error variance                0.260261             NaN

## Principal Component Analysis

[Text]

In [27]:
# Creating correlation matrix
x_mx = happiness.drop(columns = ['Country name', 'year'])
corr_mx = x_mx.corr()

In [28]:
corr_mx.loc[:, 'Life Ladder'].sort_values()

Perceptions of corruption          -0.431500
Negative affect                    -0.339969
Generosity                          0.181630
Positive affect                     0.518169
Freedom to make life choices        0.534493
Healthy life expectancy at birth    0.713499
Social support                      0.721662
Log GDP per capita                  0.784868
Life Ladder                         1.000000
Name: Life Ladder, dtype: float64

In [29]:
# Melting corr_mx
corr_mx_long = corr_mx.reset_index().rename(
    columns = {'index': 'row'}
).melt(
    id_vars = 'row',
    var_name = 'col',
    value_name = 'Correlation'
)

# Constructing heatmap
alt.Chart(corr_mx_long).mark_rect().encode(
    x = alt.X('col', title = '', sort = {'field': 'Correlation', 'order': 'ascending'}), 
    y = alt.Y('row', title = '', sort = {'field': 'Correlation', 'order': 'ascending'}),
    color = alt.Color('Correlation', 
                      scale = alt.Scale(scheme = 'blueorange', # diverging gradient
                                        domain = (-1, 1), # ensure white = 0
                                        type = 'sqrt'), # adjust gradient scale
                     legend = alt.Legend(tickCount = 5)) # add ticks to colorbar at 0.5 for reference
).properties(width = 300, height = 300)

alt.Chart(...)

From this heat map we can see that the variables Log GDP per Capita, Social support, and Healthy life expectancy at birth are all strongly _positively_ correlated with countries' life ladder score. Likewise, we can see that Perceptions of corruption and Negative affect are strongly _negatively_ correlated with a country's life ladder score.

In [30]:
# Checking how many rows have missing values in our data set
missing_values = x_mx.isnull()
missing_values.any(axis=1).sum()/len(x_mx)

0.10959527057753524

In order to do principal component analysis, we cannot have any missing values in our dataset. However, as seen above, approximately 11% of our observations have one or more missing values. In order to deal with this missingness we decided to delete the rows containing missing values. We did not feel mean imputation was appropriate because variable values can differ so much between countries and/or regions. Thus, we did not think that substituting an overall mean of each variable to fill missing values was the correct course of action.

In [31]:
## (i) Set index = 'Region'
x_mx_id = happ.drop(columns = ['Country name', 'year', 'Life Ladder']).set_index(['Region', 'Period'])

## (ii) Removing rows with missing values
x_mx_nona = x_mx_id.dropna()

## (iii) center and scale for the PCA
x_mx_nona = (x_mx_nona - x_mx_nona.mean())/x_mx_nona.std()

## (iv) fit, components = 8 because life ladder was removed
pca = PCA(8)
pca.fit(x_mx_nona)

## (v) Computing variance ratios
var_ratios = pca.explained_variance_ratio_

# (vi) Creating dataframe with proportion of variance explained by each comonent and cumulative sum
pca_var_explained = pd.DataFrame({
    'Component': np.arange(1, 9),
    'Proportion of variance explained': var_ratios})
pca_var_explained['Cumulative variance explained'] = var_ratios.cumsum()

pca_var_explained

Component  Proportion of variance explained  Cumulative variance explained
0          1                          0.428729                       0.428729
1          2                          0.187067                       0.615795
2          3                          0.116884                       0.732680
3          4                          0.092980                       0.825659
4          5                          0.077939                       0.903599
5          6                          0.044311                       0.947909
6          7                          0.033829                       0.981739
7          8                          0.018261                       1.000000

In [32]:
# (vii) Plotting variance explained by each component and cumulitave variance
base = alt.Chart(pca_var_explained).encode(
    x = 'Component')

prop_var_base = base.encode(
    y = alt.Y('Proportion of variance explained',
              axis = alt.Axis(titleColor = '#57A44C'))
)

cum_var_base = base.encode(
    y = alt.Y('Cumulative variance explained', axis = alt.Axis(titleColor = '#5276A7'))
)

prop_var = prop_var_base.mark_line(stroke = '#57A44C') + prop_var_base.mark_point(color = '#57A44C')
cum_var = cum_var_base.mark_line() + cum_var_base.mark_point()

var_explained_plot = alt.layer(prop_var, cum_var).resolve_scale(y = 'independent')

# display
var_explained_plot

alt.LayerChart(...)

From this graph, we decided to use 4 principal componenets as over 80% of total variance can be explained by these 4 componenets.

In [33]:
## (viii) Subsetting only the 4 component loadings that we chose
loading_df = pd.DataFrame(pca.components_.transpose()).iloc[:,0:4].rename(columns = {0:'PC1', 1:'PC2',2:'PC3',3:'PC4'})
loading_df['Variable'] = x_mx_nona.columns

loading_df = loading_df[['Variable', 'PC1', 'PC2', 'PC3', 'PC4']]
loading_df

Variable       PC1       PC2       PC3       PC4
0                Log GDP per capita -0.424241 -0.412897  0.168809  0.030832
1                    Social support -0.431995 -0.231563 -0.250556 -0.227961
2  Healthy life expectancy at birth -0.398534 -0.400562  0.318742 -0.072395
3      Freedom to make life choices -0.391059  0.304756  0.127579 -0.116397
4                        Generosity -0.151105  0.567946  0.311961 -0.140905
5         Perceptions of corruption  0.319166 -0.243380 -0.293898 -0.732615
6                   Positive affect -0.344344  0.362144 -0.205734 -0.469475
7                   Negative affect  0.279948 -0.098095  0.751552 -0.388983

In [34]:
# (ix) Plotting each principal component's loadings
loading_plot_df = loading_df.melt(
    id_vars = 'Variable',
    var_name = 'Principal Component',
    value_name = 'Loading'
).rename(columns = {'index': 'Variable'})

loading_plot_df['zero'] = np.repeat(0, len(loading_plot_df))

base = alt.Chart(loading_plot_df)

loadings = base.mark_line(point = True).encode(
    y = alt.Y('Variable', title = ''),
    x = 'Loading',
    color = 'Principal Component'
)

rule = base.mark_rule().encode(x = alt.X('zero', title = 'Loading'), size = alt.value(0.05))

loading_plot = (loadings + rule).properties(width = 90)

loading_plot.facet(column = alt.Column('Principal Component', title = ''))

alt.FacetChart(...)

In [35]:
## (x) project pcdata onto first four components; store as data frame

# retrieve principal component scores for pc1, pc2, pc3 and pc4
projected = pd.DataFrame(
    pca.fit_transform(x_mx_nona)
).iloc[:,:4].rename(
    columns = {0:'PC1', 1:'PC2', 2:'PC3', 3:'PC4'}
)

# adjust index to align with x_mx_nona
projected.index = x_mx_nona.index
projected = projected.reset_index()

# display for preview
projected

## (xi) construct scatterplot
projected_plot = projected.copy()
projected_plot = projected_plot[(projected_plot['Region'] == 'Africa') | (projected_plot['Region'] == 'Americas')]
base = alt.Chart(projected_plot)
fig10 = base.mark_point(opacity = 0.3).encode(
    x = alt.X('PC1', title = 'PC1'),
    y = alt.Y('PC2', title = 'PC2'),
    color = alt.Color('Region:N', legend=alt.Legend(title='Region'))
).properties(
    title = 'Figure 10: Africa and American countries with PC2 plotted against PC1'
)

# display
fig10

alt.Chart(...)

Within a principal component, the variables with the largest loadings/weights (in terms of absolute value) are the ones that are most influential to that component. And since these componenets together capture over 80% of the total variation in the data, the heaviest weighted variables in each componenet are the ones that drive variation in our data.

We interpreted the first principal component (PC1) as a representation of the difference between well-being and danger. This is because, in PC1, the variables that are most influential are: Life ladder(positive), Log GDP per capita (positive), Social support (positive), Perceptions of corruption (negative), and Negative affect (negative). This means that a country with a larger value of PC1 would have a higher than average life ladder score, log GDP per capita, and social support while also having a lower than average perception of corruption and negative affect score. Likewise, a country with a smaller value of PC1 would have a lower than average life ladder score, log GDP per capita, and social support while also having a higher than average perception of corruption and negative affect score. 

Next, we interpreted the second principal component (PC2) as a reprentation of the difference between people's willingness to help others and a country's overall wealth. This is because, in PC2, the variables that are most influential are: Generosity (positive), Positive affect (positive), Log GDP per capita (negative), and Healthy life expectancy at birth (negative). This means that a country with a larger value of PC2 would have a higher than average Generosity score and Positive affect score while also having a lower than average Log GDP per capita and Healthy life expectancy at birth. Likewise, a country with a smaller value of PC2 would have a lower than average Generosity score and Positive affect score while also having a higher than average Log GDP per capita and Healthy life expectancy at birth.

Then, we interpreted the third principal component (PC3) as a representaion of the average between people's generosity and negative feelings. This is because, in PC3, the variables that are most influential are Negative affect (positive) and Generosity (positive). This means that a country with a larger value of PC3 would have a higher than average Negative affect score and Generosity score. Likewise, a country with a smaller value of PC3 would have a lower than average  Negative affect score and Generosity score.

Finally, we interpreted the fourth principal component (PC4) as a representation of the average between people's perceptions of corruption, positive feelings, and negative feelings. This is because, in PC4, the variables that are most influential are Perceptions of corruption (negative), Positive affect (negative), and Negative affect (negative). This means that a country with a larger value of PC4 would have a higher than average Perception of corruption, Positive affect score, and Negative affect score. Likewise, a country with a smaller value of PC4 would have a lower than average Perception of corruption, Positive affect score, and Negative affect score.

_So, from this principal componenet analysis we have determined that the variables that drive the most variation in our data are Life Ladder, Log GDP per capita, Social support, Generosity, Negative affect, and Perceptions of corruption._

## Summary of findings

Throughout this project we have found that there has been a slight increase in overall happiness in the world. [INSERT BREAKDOWN BY COUNTRY/REGION HERE IF YOU WANT]. We also found that the variables that drove the variation in our data were: Life Ladder, Log GDP per capita, Social support, Generosity, Negative affect, and Perceptions of corruption. [INSERT ANY OTHER FINDINGS FROM REGRESSION HERE]